In [93]:
import pandas as pd
import numpy as np
import scipy as sp 
from fuzzywuzzy import process, fuzz
from sklearn.metrics.pairwise import cosine_similarity

pd.set_option('display.max_columns', None)

In [94]:
animes = pd.read_csv('./anime_data_2006_2022_cleaned.csv')

In [95]:
animes = animes[animes['type'] == 'TV'].reset_index(drop=True)

In [96]:
animes[animes['title'].duplicated()]

Empty DataFrame
Columns: [mal_id, url, title, title_english, title_japanese, title_synonyms, type, source, episodes, status, airing, duration, rating, score, scored_by, rank, popularity, members, favorites, synopsis, background, year, season, producers, licensors, studios, genres, themes, demographics, image_url, trailer_url, aired_date, broadcast_day_and_time, start_date]
Index: []

In [97]:
animes[animes['title'].isnull()]

Empty DataFrame
Columns: [mal_id, url, title, title_english, title_japanese, title_synonyms, type, source, episodes, status, airing, duration, rating, score, scored_by, rank, popularity, members, favorites, synopsis, background, year, season, producers, licensors, studios, genres, themes, demographics, image_url, trailer_url, aired_date, broadcast_day_and_time, start_date]
Index: []

In [98]:
animes['f_col'] = animes['genres'] + ',' + animes['themes'] + ',' + animes['demographics']

In [99]:
normalizied_df = animes[['score', 'rank', 'popularity', 'scored_by', 'members', 'favorites']]

In [100]:
normalizied_df

score     rank  popularity  scored_by  members  favorites
0      8.16    413.0         128   672279.0  1110503      34094
1      8.94     15.0         139   391827.0  1052162      58905
2      8.03    573.0         155   487522.0   993437      18516
3      7.83    888.0         179   475447.0   909771      15321
4      7.88    809.0         229   391899.0   797940      21247
...     ...      ...         ...        ...      ...        ...
5023    NaN  18727.0       23075        NaN       76          0
5024    NaN  13523.0       23028        NaN       76          0
5025    NaN  18117.0       26077        NaN       25          0
5026    NaN  18127.0       26078        NaN       25          0
5027    NaN  18118.0       26080        NaN       24          0

[5028 rows x 6 columns]

In [101]:
normalizied_df = normalizied_df.apply(lambda x: (x-np.mean(x))/(np.max(x)-np.min(x)), axis=1)

In [102]:
normalizied_df

score      rank  popularity  scored_by   members  favorites
0    -0.272758 -0.272393   -0.272650   0.332622  0.727242  -0.242063
1    -0.238084 -0.238078   -0.237960   0.134313  0.761916  -0.182107
2    -0.251681 -0.251112   -0.251533   0.239058  0.748319  -0.233051
3    -0.256764 -0.255797   -0.256576   0.265833  0.743236  -0.239932
4    -0.253172 -0.252168   -0.252895   0.237961  0.746828  -0.226554
...        ...       ...         ...        ...       ...        ...
5023       NaN  0.357855    0.546284        NaN -0.450423  -0.453716
5024       NaN  0.189606    0.602365        NaN -0.394335  -0.397635
5025       NaN  0.270823    0.576073        NaN -0.422969  -0.423927
5026       NaN  0.271091    0.575984        NaN -0.423058  -0.424016
5027       NaN  0.270801    0.576093        NaN -0.422987  -0.423907

[5028 rows x 6 columns]

In [103]:
df = pd.merge(animes[['f_col']], normalizied_df, left_index=True, right_index=True)

In [104]:
df.fillna(0, inplace=True)

In [105]:
df.head()

f_col     score      rank  \
0  Comedy,Romance,Crossdressing,Reverse Harem,Sch... -0.272758 -0.272393   
1  Action,Comedy,Sci-Fi,Gag Humor,Historical,Paro... -0.238084 -0.238078   
2           Action,Adult Cast,Organized Crime,Seinen -0.251681 -0.251112   
3  Award Winning,Comedy,Mystery,Sci-Fi,School,Others -0.256764 -0.255797   
4  Horror,Mystery,Supernatural,Gore,Psychological... -0.253172 -0.252168   

   popularity  scored_by   members  favorites  
0   -0.272650   0.332622  0.727242  -0.242063  
1   -0.237960   0.134313  0.761916  -0.182107  
2   -0.251533   0.239058  0.748319  -0.233051  
3   -0.256576   0.265833  0.743236  -0.239932  
4   -0.252895   0.237961  0.746828  -0.226554

In [106]:
df = pd.concat([df.drop('f_col', axis=1), df['f_col'].str.get_dummies(sep=',')], axis=1)

In [107]:
df.head()

score      rank  popularity  scored_by   members  favorites  Action  \
0 -0.272758 -0.272393   -0.272650   0.332622  0.727242  -0.242063       0   
1 -0.238084 -0.238078   -0.237960   0.134313  0.761916  -0.182107       1   
2 -0.251681 -0.251112   -0.251533   0.239058  0.748319  -0.233051       1   
3 -0.256764 -0.255797   -0.256576   0.265833  0.743236  -0.239932       0   
4 -0.253172 -0.252168   -0.252895   0.237961  0.746828  -0.226554       0   

   Adult Cast  Adventure  Anthropomorphic  Avant Garde  Award Winning  \
0           0          0                0            0              0   
1           0          0                0            0              0   
2           1          0                0            0              0   
3           0          0                0            0              1   
4           0          0                0            0              0   

   Boys Love  CGDCT  Childcare  Combat Sports  Comedy  Crossdressing  \
0          0      0          0              0       1              1   
1          0      0          0              0       1              0   
2          0      0          0              0       0              0   
3          0      0          0              0       1              0   
4          0      0          0              0       0              0   

   Delinquents  Detective  Drama  Ecchi  Educational  Erotica  Fantasy  \
0            0          0      0      0            0        0        0   
1            0          0      0      0            0        0        0   
2            0          0      0      0            0        0        0   
3            0          0      0      0            0        0        0   
4            0          0      0      0            0        0        0   

   Gag Humor  Girls Love  Gore  Gourmet  Harem  High Stakes Game  Historical  \
0          0           0     0        0      0                 0           0   
1          1           0     0        0      0                 0           1   
2          0           0     0        0      0                 0           0   
3          0           0     0        0      0                 0           0   
4          0           0     1        0      0                 0           0   

   Horror  Idols (Female)  Idols (Male)  Isekai  Iyashikei  Josei  Kids  \
0       0               0             0       0          0      0     0   
1       0               0             0       0          0      0     0   
2       0               0             0       0          0      0     0   
3       0               0             0       0          0      0     0   
4       1               0             0       0          0      0     0   

   Love Polygon  Magical Sex Shift  Mahou Shoujo  Martial Arts  Mecha  \
0             0                  0             0             0      0   
1             0                  0             0             0      0   
2             0                  0             0             0      0   
3             0                  0             0             0      0   
4             0                  0             0             0      0   

   Medical  Military  Music  Mystery  Mythology  Organized Crime  \
0        0         0      0        0          0                0   
1        0         0      0        0          0                0   
2        0         0      0        0          0                1   
3        0         0      0        1          0                0   
4        0         0      0        1          0                0   

   Otaku Culture  Others  Parody  Performing Arts  Pets  Psychological  \
0              0       0       0                0     0              0   
1              0       0       1                0     0              0   
2              0       0       0                0     0              0   
3              0       1       0                0     0              0   
4              0       1       0                0     0              1   

 

In [108]:
piv_sparse = sp.sparse.csr_matrix(df.values)

In [109]:
anime_similarity = cosine_similarity(piv_sparse)

In [110]:
ani_sim_df = pd.DataFrame(anime_similarity, index = animes['title'], columns = animes['title'])

In [111]:
ani_sim_df

title                              Ouran High School Host Club   Gintama  \
title                                                                      
Ouran High School Host Club                           1.000000  0.235431   
Gintama                                               0.235431  1.000000   
Black Lagoon                                          0.152710  0.278892   
The Melancholy of Haruhi Suzumiya                     0.419845  0.363570   
Higurashi: When They Cry                              0.128291  0.105900   
...                                                        ...       ...   
Super Wings 6                                        -0.090092 -0.081884   
Tea Tea Cherry                                       -0.071163 -0.064674   
Bai Bian Xiao Ba 10th Season                         -0.085390 -0.077597   
Bai Bian Xiao Ba 9th Season                          -0.085406 -0.077612   
Bai Bian Xiao Ba 11th Season                         -0.085393 -0.077600   

title                              Black Lagoon  \
title                                             
Ouran High School Host Club            0.152710   
Gintama                                0.278892   
Black Lagoon                           1.000000   
The Melancholy of Haruhi Suzumiya      0.150295   
Higurashi: When They Cry               0.148816   
...                                         ...   
Super Wings 6                         -0.106209   
Tea Tea Cherry                        -0.083897   
Bai Bian Xiao Ba 10th Season          -0.100674   
Bai Bian Xiao Ba 9th Season           -0.100693   
Bai Bian Xiao Ba 11th Season          -0.100679   

title                              The Melancholy of Haruhi Suzumiya  \
title                                                                  
Ouran High School Host Club                                 0.419845   
Gintama                                                     0.363570   
Black Lagoon                                                0.150295   
The Melancholy of Haruhi Suzumiya                           1.000000   
Higurashi: When They Cry                                    0.417481   
...                                                              ...   
Super Wings 6                                              -0.089099   
Tea Tea Cherry                                              0.105263   
Bai Bian Xiao Ba 10th Season                               -0.084462   
Bai Bian Xiao Ba 9th Season                                -0.084477   
Bai Bian Xiao Ba 11th Season                               -0.084465   

title                              Higurashi: When They Cry      Nana  \
title                                                                   
Ouran High School Host Club                        0.128291  0.414198   
Gintama                                            0.105900  0.103980   
Black Lagoon                                       0.148816  0.317930   
The Melancholy of Haruhi Suzumiya                  0.417481  0.121856   
Higurashi: When They Cry                           1.000000  0.121094   
...                                                     ...       ...   
Super Wings 6                                     -0.090086 -0.092041   
Tea Tea Cherry                                     0.104746 -0.072691   
Bai Bian Xiao Ba 10th Season                      -0.085392 -0.087225   
Bai Bian Xiao Ba 9th Season                       -0.085408 -0.087241   
Bai Bian Xiao Ba 11th Season                      -0.085396 -0.087228   

title                              Air Gear  xxxHOLiC  Utawarerumono  \
title                                                                  
Ouran High School Host Club        0.419515  0.269124       0.133884   
Gintama                            0.363503  0.233545       0.392483   
Black Lagoon                       0.149945  0.318659       0.345032   
The Melancholy of Haruhi Suzumiya  0.418197  0.560674       0.448960   
Higurashi: When They Cry    

In [112]:
# print(ani_sim_df['Digimon Fusion']['Drifters'])

In [113]:
# print(isinstance(ani_sim_df['Drifters']['Digimon Fusion'], pd.Series))

In [114]:
# print(isinstance(ani_sim_df['Drifters']['Drifters'], float))

In [115]:
titles = animes[animes['type'] == 'TV']['title'].unique().tolist()

In [116]:
ani_sim_df['Nisekoi: False Love']

title
Ouran High School Host Club          0.611975
Gintama                              0.393333
Black Lagoon                         0.164377
The Melancholy of Haruhi Suzumiya    0.453583
Higurashi: When They Cry             0.138076
                                       ...   
Super Wings 6                       -0.095424
Tea Tea Cherry                      -0.075396
Bai Bian Xiao Ba 10th Season        -0.090467
Bai Bian Xiao Ba 9th Season         -0.090483
Bai Bian Xiao Ba 11th Season        -0.090470
Name: Nisekoi: False Love, Length: 5028, dtype: float64

In [117]:
ani_sim_df.to_pickle('anime_similarity_v2.pkl')

In [118]:
def anime_recommendation(ani_name):
    ani_name = process.extract(ani_name, titles, scorer=fuzz.token_set_ratio)[0][0]
    number = 1
    print(f'If you like {ani_name}, how about watching these 🤗 :\n')
    # return ani_sim_df.sort_values(by=ani_name, ascending=False).index[1:17]
    for anime in ani_sim_df.sort_values(by = ani_name, ascending = False).index[1:17]:
        print(f'#{number} => {anime}, {round(ani_sim_df[anime][ani_name]*100,2)}% match')
        number +=1  

anime_recommendation('Haikyuu!!')

If you like Haikyu!!, how about watching these 🤗 :

#1 => Kuroko's Basketball 3, 99.99% match
#2 => Haikyu!! To the Top, 99.99% match
#3 => Kuroko's Basketball, 99.99% match
#4 => Kuroko's Basketball 2, 99.99% match
#5 => Haikyu!! To the Top 2nd-cour, 99.99% match
#6 => Haikyu!! 2nd Season, 99.98% match
#7 => Haikyu!! 3rd Season, 99.98% match
#8 => Ace of Diamond: Second Season, 99.96% match
#9 => Ace of Diamond Act II, 99.86% match
#10 => Ace of Diamond, 99.81% match
#11 => Days_32494, 99.78% match
#12 => Ahiru no Sora, 99.71% match
#13 => The Knight in the Area, 90.77% match
#14 => Baby Steps 2nd Season, 89.26% match
#15 => Major S3, 89.26% match
#16 => Major S4, 89.25% match


In [119]:
anime_recommendation('Grand Blue Dreaming')

If you like Grand Blue Dreaming, how about watching these 🤗 :

#1 => Servant x Service, 88.97% match
#2 => Police in a Pod, 88.71% match
#3 => The Laughing Salesman, 86.17% match
#4 => Genshiken 2, 81.2% match
#5 => Rec, 81.14% match
#6 => Genshiken Second Season, 80.81% match
#7 => Wave, Listen to Me!, 80.63% match
#8 => Thermæ Romæ, 80.2% match
#9 => One Punch Man, 75.37% match
#10 => One Punch Man Season 2, 75.28% match
#11 => Moyashimon, 74.57% match
#12 => Lupin the Third Part 5, 74.41% match
#13 => Lupin the Third Part 4, 74.29% match
#14 => Space Brothers, 74.16% match
#15 => Tonari no Seki-kun: The Master of Killing Time, 74.06% match
#16 => Mr. Tonegawa: Middle Management Blues, 74.03% match


In [120]:
anime_recommendation('Violet Evergarden')

If you like Violet Evergarden, how about watching these 🤗 :

#1 => The Day I Became a God, 99.89% match
#2 => Lost Song, 99.74% match
#3 => The Beast Player Erin, 98.99% match
#4 => Wonder Egg Priority, 89.0% match
#5 => Kino's Journey -the Beautiful World- the Animated Series, 88.82% match
#6 => Tales of the Abyss, 88.81% match
#7 => Utawarerumono: The False Faces, 88.8% match
#8 => Yuki Yuna is a Hero, 88.69% match
#9 => Yuki Yuna is a Hero: The Hero Chapter, 88.55% match
#10 => Yuki Yuna is a Hero: The Washio Sumi Chapter, 88.51% match
#11 => Celestial Method, 88.39% match
#12 => Yuki Yuna is a Hero: The Great Mankai Chapter, 87.37% match
#13 => Utawarerumono: Mask of Truth, 87.33% match
#14 => Umi Monogatari, 86.98% match
#15 => Assassins Pride, 86.12% match
#16 => D_Cide Traumerei the Animation, 85.56% match


In [121]:
anime_recommendation('Hunter x Hunter')

If you like Hunter x Hunter, how about watching these 🤗 :

#1 => Fairy Tail, 99.98% match
#2 => The Seven Deadly Sins: Revival of the Commandments, 99.96% match
#3 => The Seven Deadly Sins: Signs of Holy War, 99.96% match
#4 => The Seven Deadly Sins, 99.96% match
#5 => Fairy Tail Series 2, 99.96% match
#6 => The Seven Deadly Sins: Imperial Wrath of the Gods, 99.95% match
#7 => Magi: The Kingdom of Magic, 99.94% match
#8 => Magi: Adventure of Sinbad, 99.93% match
#9 => Magi: The Labyrinth of Magic, 99.93% match
#10 => Bleach: Thousand-Year Blood War, 99.92% match
#11 => Fairy Tail Final Series, 99.87% match
#12 => The Seven Deadly Sins: Dragon's Judgement, 99.83% match
#13 => Dragon Quest: The Adventure of Dai, 99.39% match
#14 => Is It Wrong to Try to Pick Up Girls in a Dungeon?, 91.12% match
#15 => Is It Wrong to Try to Pick Up Girls in a Dungeon? II, 91.1% match
#16 => Is It Wrong to Try to Pick Up Girls in a Dungeon? III, 91.05% match


In [122]:
anime_recommendation('Gintama')

If you like Gintama, how about watching these 🤗 :

#1 => Gintama Season 4, 99.99% match
#2 => Gintama Season 2, 99.97% match
#3 => Gintama Season 5, 99.94% match
#4 => Gintama.: Silver Soul Arc - Second Half War, 99.92% match
#5 => Gintama.: Silver Soul Arc, 99.91% match
#6 => Gintama: Enchousen, 99.89% match
#7 => Gintama.: Slip Arc, 99.89% match
#8 => Level E, 73.82% match
#9 => Naruto Spin-Off: Rock Lee & His Ninja Pals, 73.72% match
#10 => Sayonara, Zetsubou-Sensei, 67.2% match
#11 => Love After World Domination, 67.19% match
#12 => Zan Sayonara Zetsubou Sensei, 67.19% match
#13 => Zoku Sayonara Zetsubou Sensei, 67.18% match
#14 => Good Luck Girl!, 67.17% match
#15 => Senyuu., 67.17% match
#16 => Senyuu. 2, 66.99% match


In [123]:
anime_recommendation('Laid-Back Camp')

If you like Laid-Back Camp, how about watching these 🤗 :

#1 => Laid-Back Camp Season 2, 100.0% match
#2 => Room Camp, 99.99% match
#3 => Tamayura: Hitotose, 99.68% match
#4 => Tamayura: More Aggressive, 99.42% match
#5 => Is the Order a Rabbit??, 91.03% match
#6 => Is the Order a Rabbit?, 90.98% match
#7 => Super Cub, 90.98% match
#8 => Is the Order a Rabbit? Bloom, 90.88% match
#9 => Slow Loop, 90.84% match
#10 => Encouragement of Climb Season 2, 90.84% match
#11 => Encouragement of Climb, 90.83% match
#12 => Encouragement of Climb Season 3, 90.6% match
#13 => Sketchbook ~full color's~, 90.49% match
#14 => Encouragement of Climb: Next Summit, 90.2% match
#15 => Tamako Market, 89.05% match
#16 => Play It Cool, Guys, 88.81% match


In [124]:
anime_recommendation('Drifters')

If you like Drifters, how about watching these 🤗 :

#1 => Golden Kamuy Season 3, 76.06% match
#2 => Golden Kamuy, 76.04% match
#3 => Golden Kamuy Season 2, 76.04% match
#4 => Golden Kamuy Season 4, 75.94% match
#5 => Berserk: Season II, 66.93% match
#6 => Berserk (2016), 66.92% match
#7 => Lupin the Third: The Woman Called Fujiko Mine, 66.79% match
#8 => Berserk: The Golden Age Arc - Memorial Edition, 66.79% match
#9 => Tsukimichi -Moonlit Fantasy-, 64.98% match
#10 => Jormungand Season 2: Perfect Order, 64.98% match
#11 => GATE, 64.98% match
#12 => Dorohedoro, 64.98% match
#13 => Vinland Saga, 64.97% match
#14 => GATE Part 2, 64.96% match
#15 => Brave 10, 64.95% match
#16 => Jormungand, 64.93% match


In [125]:
anime_recommendation('Death Note')

If you like Death Note, how about watching these 🤗 :

#1 => Talentless Nana, 82.82% match
#2 => Platinum End, 70.84% match
#3 => Mouryou no Hako, 70.18% match
#4 => The Future Diary, 67.75% match
#5 => Terror in Resonance, 66.1% match
#6 => Tomodachi Game, 66.02% match
#7 => Summer Time Rendering, 65.55% match
#8 => Dr. Ramune -Mysterious Disease Specialist-, 65.41% match
#9 => Ghost Hound, 64.89% match
#10 => ERASED, 61.53% match
#11 => The Promised Neverland Season 2, 61.03% match
#12 => Rampo Kitan: Game of Laplace, 60.52% match
#13 => Ga-Rei-Zero, 60.52% match
#14 => Neuro: Supernatural Detective, 60.44% match
#15 => Babylon, 60.17% match
#16 => The Promised Neverland, 57.56% match


In [126]:
anime_recommendation('Made in Abyss')

If you like Made in Abyss, how about watching these 🤗 :

#1 => Made in Abyss: The Golden City of the Scorching Sun, 94.74% match
#2 => Sunday Without God, 81.29% match
#3 => Tower of God, 75.25% match
#4 => Children of the Whales, 75.15% match
#5 => Den-noh Coil, 74.83% match
#6 => Afterlost, 74.52% match
#7 => Tales of the Abyss, 74.01% match
#8 => Kino's Journey -the Beautiful World- the Animated Series, 74.0% match
#9 => Fractale, 74.0% match
#10 => El Cazador de la Bruja, 73.78% match
#11 => Jyu-Oh-Sei: Planet of the Beast King, 70.11% match
#12 => Otherside Picnic, 69.89% match
#13 => Goblin Slayer, 67.57% match
#14 => Rokka: Braves of the Six Flowers, 67.54% match
#15 => Digimon Data Squad, 67.51% match
#16 => WorldEnd: What do you do at the end of the world? Are you busy? Will you save us?, 67.49% match


In [127]:
anime_recommendation('Your Lie in April')

If you like Your Lie in April, how about watching these 🤗 :

#1 => Fuuka, 93.35% match
#2 => Domestic Girlfriend, 92.49% match
#3 => Kono Oto Tomare!: Sounds of Life Season 2, 85.47% match
#4 => Kono Oto Tomare!: Sounds of Life, 85.18% match
#5 => Anonymous Noise, 85.15% match
#6 => A Town Where You Live, 84.03% match
#7 => Those Snow White Notes, 84.01% match
#8 => Kids on the Slope, 79.69% match
#9 => Toradora!, 76.89% match
#10 => Scum's Wish, 76.69% match
#11 => Love and Lies, 76.66% match
#12 => True Tears, 76.64% match
#13 => O Maidens in Your Savage Season, 76.61% match
#14 => White Album 2, 76.6% match
#15 => Just Because!, 76.49% match
#16 => Flowers of Evil, 76.29% match


In [128]:
anime_recommendation('Daily Lives of High School Boys')

If you like Daily Lives of High School Boys, how about watching these 🤗 :

#1 => Kill Me Baby, 99.91% match
#2 => SHIMONETA: A Boring World Where the Concept of Dirty Jokes Doesn't Exist, 91.11% match
#3 => Place to Place, 91.04% match
#4 => Wasteful Days of High School Girls, 90.9% match
#5 => Yuyushiki, 90.82% match
#6 => Ani ni Tsukeru Kusuri wa Nai! 2, 89.1% match
#7 => GJ Club, 89.09% match
#8 => Please tell me! Galko-chan, 89.08% match
#9 => Ani ni Tsukeru Kusuri wa Nai!, 89.07% match
#10 => Ani ni Tsukeru Kusuri wa Nai! 3, 89.05% match
#11 => Komori-san Can't Decline!, 88.92% match
#12 => Ani ni Tsukeru Kusuri wa Nai! 4, 88.89% match
#13 => Outburst Dreamer Boys, 88.7% match
#14 => Megane-bu!, 87.97% match
#15 => Wagamama High Spec, 87.73% match
#16 => Teppen—!!!!!!!!!!!!!!! Laughing 'til You Cry, 87.14% match


In [129]:
anime_recommendation('konosuba')

If you like KonoSuba: God's Blessing on This Wonderful World!, how about watching these 🤗 :

#1 => KonoSuba: God's Blessing on This Wonderful World! 2, 100.0% match
#2 => Cautious Hero: The Hero Is Overpowered but Overly Cautious, 87.38% match
#3 => Life with an Ordinary Guy who Reincarnated into a Total Fantasy Knockout, 87.15% match
#4 => Isekai Quartet 2, 86.5% match
#5 => Isekai Quartet, 86.48% match
#6 => Didn't I Say to Make My Abilities Average in the Next Life?!, 86.41% match
#7 => Kuma Kuma Kuma Bear, 86.39% match
#8 => In the Land of Leadale, 86.37% match
#9 => In Another World With My Smartphone, 82.35% match
#10 => So I'm a Spider, So What?, 82.24% match
#11 => Tsukimichi -Moonlit Fantasy-, 79.91% match
#12 => The Eminence in Shadow, 79.89% match
#13 => Reincarnated as a Sword, 79.83% match
#14 => I've Been Killing Slimes for 300 Years and Maxed Out My Level, 79.81% match
#15 => The Faraway Paladin, 79.74% match
#16 => Digimon Fusion, 79.72% match


In [130]:
anime_recommendation('jujutsu')
%time

If you like Jujutsu Kaisen, how about watching these 🤗 :

#1 => Demon Slayer: Kimetsu no Yaiba, 83.24% match
#2 => Blue Exorcist, 83.15% match
#3 => Blue Exorcist: Kyoto Saga, 83.03% match
#4 => Soul Eater, 82.98% match
#5 => Soul Eater NOT!, 82.87% match
#6 => Buso Renkin, 82.8% match
#7 => My Hero Academia Season 2, 72.85% match
#8 => My Hero Academia, 72.85% match
#9 => My Hero Academia Season 3, 72.83% match
#10 => Demon Slayer: Kimetsu no Yaiba Entertainment District Arc, 72.78% match
#11 => My Hero Academia Season 4, 72.78% match
#12 => Assassination Classroom Second Season, 72.77% match
#13 => Noragami Aragoto, 72.76% match
#14 => Demon Slayer: Kimetsu no Yaiba Mugen Train Arc, 72.73% match
#15 => Assassination Classroom, 72.71% match
#16 => Noragami, 72.7% match
CPU times: user 1e+03 ns, sys: 1e+03 ns, total: 2 µs
Wall time: 4.05 µs


In [131]:
ani_sim_df['Haikyu!!']

title
Ouran High School Host Club          0.329603
Gintama                              0.279137
Black Lagoon                         0.181483
The Melancholy of Haruhi Suzumiya    0.326256
Higurashi: When They Cry             0.152469
                                       ...   
Super Wings 6                       -0.107491
Tea Tea Cherry                      -0.084901
Bai Bian Xiao Ba 10th Season        -0.101874
Bai Bian Xiao Ba 9th Season         -0.101893
Bai Bian Xiao Ba 11th Season        -0.101878
Name: Haikyu!!, Length: 5028, dtype: float64

In [132]:
anime_recommendation('haikyuu')

If you like Haikyu!!, how about watching these 🤗 :

#1 => Kuroko's Basketball 3, 99.99% match
#2 => Haikyu!! To the Top, 99.99% match
#3 => Kuroko's Basketball, 99.99% match
#4 => Kuroko's Basketball 2, 99.99% match
#5 => Haikyu!! To the Top 2nd-cour, 99.99% match
#6 => Haikyu!! 2nd Season, 99.98% match
#7 => Haikyu!! 3rd Season, 99.98% match
#8 => Ace of Diamond: Second Season, 99.96% match
#9 => Ace of Diamond Act II, 99.86% match
#10 => Ace of Diamond, 99.81% match
#11 => Days_32494, 99.78% match
#12 => Ahiru no Sora, 99.71% match
#13 => The Knight in the Area, 90.77% match
#14 => Baby Steps 2nd Season, 89.26% match
#15 => Major S3, 89.26% match
#16 => Major S4, 89.25% match


In [133]:
anime_recommendation('kaguya-sama')

If you like Kaguya-sama: Love is War, how about watching these 🤗 :

#1 => Kaguya-sama: Love is War Season 2, 100.0% match
#2 => How clumsy you are, Miss Ueno., 90.89% match
#3 => Tonari no Seki-kun: The Master of Killing Time, 81.2% match
#4 => Potemayo, 79.67% match
#5 => Hi Score Girl II, 76.86% match
#6 => Hi Score Girl, 76.73% match
#7 => Ishida and Asakura, 76.58% match
#8 => Magical Sempai, 76.54% match
#9 => Wagnaria!!2, 72.67% match
#10 => Himouto! Umaru-chan, 72.62% match
#11 => Kaguya-sama: Love is War - Ultra Romantic, 72.61% match
#12 => Teasing Master Takagi-san 2, 72.6% match
#13 => Don't Toy with Me, Miss Nagatoro, 72.58% match
#14 => Komi Can't Communicate, 72.55% match
#15 => D-Frag!, 72.51% match
#16 => Himouto! Umaru-chan R, 72.51% match


In [134]:
anime_recommendation('fruits basket')

If you like Fruits Basket 1st Season, how about watching these 🤗 :

#1 => Fruits Basket 2nd Season, 92.41% match
#2 => Kokoro Connect, 85.42% match
#3 => Anonymous Noise, 85.31% match
#4 => Kimi ni Todoke: From Me to You, 84.15% match
#5 => Bokura ga Ita, 84.14% match
#6 => Blue Spring Ride, 84.13% match
#7 => Say "I Love You.", 84.12% match
#8 => Kimi ni Todoke: From Me to You Season 2, 84.08% match
#9 => Vampire Knight, 79.82% match
#10 => Vampire Knight Guilty, 79.82% match
#11 => Orange, 79.8% match
#12 => Clannad, 76.65% match
#13 => Scum's Wish, 76.64% match
#14 => Love and Lies, 76.62% match
#15 => Fruits Basket: The Final Season, 76.62% match
#16 => Domestic Girlfriend, 76.62% match


In [135]:
anime_recommendation('bunny girl senpai')

If you like Rascal Does Not Dream of Bunny Girl Senpai, how about watching these 🤗 :

#1 => Clannad, 99.93% match
#2 => Kokoro Connect, 92.34% match
#3 => Little Busters! ~Refrain~, 92.23% match
#4 => Angel Beats!, 91.2% match
#5 => ReLIFE, 91.16% match
#6 => Clannad: After Story, 91.14% match
#7 => Myself; Yourself, 91.08% match
#8 => Kanon, 91.07% match
#9 => Bottom-Tier Character Tomozaki, 91.06% match
#10 => Sola, 90.92% match
#11 => KimiKiss: Pure Rouge, 90.91% match
#12 => Venus Versus Virus, 89.9% match
#13 => Toradora!, 83.17% match
#14 => School Days, 83.13% match
#15 => The Pet Girl of Sakurasou, 83.09% match
#16 => The Troubled Life of Miss Kotoura, 83.0% match


In [136]:
anime_recommendation('scum wish')

If you like Scum's Wish, how about watching these 🤗 :

#1 => More than a Married Couple, but Not Lovers., 91.06% match
#2 => Domestic Girlfriend, 82.94% match
#3 => Love and Lies, 82.92% match
#4 => True Tears, 82.92% match
#5 => Toradora!, 82.91% match
#6 => Sing "Yesterday" for Me, 82.91% match
#7 => Just Because!, 82.85% match
#8 => Wandering Son, 82.65% match
#9 => Hitohira, 81.73% match
#10 => Mysterious Girlfriend X, 81.16% match
#11 => Your Lie in April, 76.69% match
#12 => Kokoro Connect, 76.68% match
#13 => Fruits Basket 1st Season, 76.64% match
#14 => Anonymous Noise, 76.47% match
#15 => Kimi ni Todoke: From Me to You Season 2, 72.37% match
#16 => ReLIFE, 72.37% match


In [137]:
anime_recommendation('domestic girlfriend')

If you like Domestic Girlfriend, how about watching these 🤗 :

#1 => Your Lie in April, 92.49% match
#2 => A Town Where You Live, 90.89% match
#3 => Fuuka, 86.28% match
#4 => Toradora!, 83.14% match
#5 => Scum's Wish, 82.94% match
#6 => Love and Lies, 82.9% match
#7 => True Tears, 82.88% match
#8 => O Maidens in Your Savage Season, 82.85% match
#9 => Just Because!, 82.72% match
#10 => Flowers of Evil, 82.5% match
#11 => Horimiya, 81.4% match
#12 => School Rumble: 2nd Semester, 76.83% match
#13 => Kono Oto Tomare!: Sounds of Life Season 2, 76.76% match
#14 => Kokoro Connect, 76.71% match
#15 => Fruits Basket 1st Season, 76.62% match
#16 => Cross Game, 76.39% match


In [138]:
anime_recommendation('black clover')

If you like Black Clover, how about watching these 🤗 :

#1 => World Conquest Zvezda Plot, 90.92% match
#2 => Dragon Goes House-Hunting, 90.72% match
#3 => Toriko, 86.18% match
#4 => Fairy Tail Series 2, 82.98% match
#5 => Magi: The Kingdom of Magic, 82.98% match
#6 => The Seven Deadly Sins: Imperial Wrath of the Gods, 82.98% match
#7 => Magi: Adventure of Sinbad, 82.98% match
#8 => Fairy Tail, 82.98% match
#9 => The Seven Deadly Sins: Signs of Holy War, 82.98% match
#10 => Problem Children Are Coming from Another World, Aren't They?, 82.98% match
#11 => Magi: The Labyrinth of Magic, 82.98% match
#12 => The Seven Deadly Sins: Revival of the Commandments, 82.97% match
#13 => Soul Eater, 82.97% match
#14 => Fate/Kaleid Liner Prisma Illya 2Wei!, 82.96% match
#15 => The Seven Deadly Sins, 82.95% match
#16 => Bleach: Thousand-Year Blood War, 82.95% match
